In [5]:
from matplotlib import pyplot as plt
import os
import numpy as np
import json


file_dir = "/data03/sunyi/time_constrained_cot/outputs/2_6"
model_list = [
    "NovaSky-AI/Sky-T1-32B-Preview",
    "Qwen/QwQ-32B-Preview",
    "Qwen/Qwen2.5-72B-Instruct",
    "Qwen/Qwen2.5-32B-Instruct",
    "Qwen/Qwen2.5-14B-Instruct", 
    "Qwen/Qwen2.5-7B-Instruct", 
    "Qwen/Qwen2.5-3B-Instruct", 
    "Qwen/Qwen2.5-1.5B-Instruct",
    "Qwen/Qwen2.5-Math-1.5B-Instruct",
    "Qwen/Qwen2.5-Math-7B-Instruct",
    "mistralai/Mistral-Small-Instruct-2409",
    "mistralai/Mistral-Nemo-Instruct-2407",
    "mistralai/Ministral-8B-Instruct-2410",
    "mistralai/Mathstral-7B-v0.1",
    "google/gemma-2-27b-it",
    "google/gemma-2-9b-it",
    "google/gemma-2-2b-it",
    "microsoft/Phi-3-medium-128k-instruct",
    "microsoft/Phi-3-small-128k-instruct",
    "microsoft/Phi-3-mini-128k-instruct",
    "microsoft/Phi-3.5-mini-instruct",
    "microsoft/phi-4",
    "deepseek-ai/DeepSeek-R1-Distill-Qwen-1.5B",
    "deepseek-ai/DeepSeek-R1-Distill-Qwen-7B",
    "deepseek-ai/DeepSeek-R1-Distill-Qwen-14B",
    "deepseek-ai/DeepSeek-R1-Distill-Qwen-32B",
    "meta-llama/Llama-3.2-3B-Instruct",
    "meta-llama/Llama-3.2-1B-Instruct",
    "meta-llama/Llama-3.1-8B-Instruct",
    "meta-llama/Llama-3.1-70B-Instruct",
    
]

In [6]:
# PROMP_LIST = [ "-c2f-budget", "-aav-budget", "-sbs-budget", "-aav-budget-hard", "-c2f-budget-hard", "-sbs-budget-hard"]

# findings1
# PROMP_LIST = [ "-c2f", "-sbs", "-aav", "-sbs-hard", "-c2f-hard", "-aav-hard"]
PROMP_LIST3 = [ "-sbs", "-c2f","-aav"]


MODEL_SERIES_MAP = {
    "Qwen/QwQ-32B-Preview": "qwen",
    "Qwen/Qwen2.5-32B-Instruct": "qwen",
    "Qwen/Qwen2.5-14B-Instruct": "qwen",
    "Qwen/Qwen2.5-7B-Instruct": "qwen",
    "Qwen/Qwen2.5-3B-Instruct": "qwen",
    "Qwen/Qwen2.5-1.5B-Instruct": "qwen",
    "Qwen/Qwen2.5-Math-1.5B-Instruct": "qwen-math",
    "Qwen/Qwen2.5-Math-7B-Instruct": "qwen-math",
    # "internlm/internlm2_5-1_8b-chat": "internlm",
    # "internlm/internlm2_5-7b-chat": "internlm",
    # "internlm/internlm2_5-20b-chat": "internlm",
    "google/gemma-2-2b-it": "gemma",
    "google/gemma-2-9b-it": "gemma",
    "google/gemma-2-27b-it": "gemma",
    "mistralai/Mathstral-7B-v0.1": "mistral",
    "mistralai/Ministral-8B-Instruct-2410": "mistral",
    "mistralai/Mistral-Nemo-Instruct-2407": "mistral",
    "mistralai/Mistral-Small-Instruct-2409": "mistral",
    "microsoft/phi-4": "phi4",
    "microsoft/Phi-3-medium-128k-instruct": "phi3medium",
    "microsoft/Phi-3-small-128k-instruct": "phi3small",
    "microsoft/Phi-3.5-mini-instruct": "phi3mini",
    "microsoft/Phi-3-mini-128k-instruct": "phi3mini",
    "NovaSky-AI/Sky-T1-32B-Preview": "qwen",
    "deepseek-ai/DeepSeek-R1-Distill-Qwen-1.5B": "deepseek-r1-distill",
    "deepseek-ai/DeepSeek-R1-Distill-Qwen-7B": "deepseek-r1-distill",
    "deepseek-ai/DeepSeek-R1-Distill-Qwen-14B": "deepseek-r1-distill",
    "deepseek-ai/DeepSeek-R1-Distill-Qwen-32B": "deepseek-r1-distill",
    "deepseek-ai/DeepSeek-R1-Distill-Llama-8B": "deepseek-r1-distill",
    "meta-llama/Llama-3.2-3B-Instruct": "llama",
    "meta-llama/Llama-3.2-1B-Instruct": "llama",
    "meta-llama/Llama-3.1-8B-Instruct": "llama",
    "meta-llama/Llama-3.1-70B-Instruct": "llama",
    "Qwen/Qwen2.5-72B-Instruct": "qwen",
}


MODEL_SERIES_PROMPT_TYPE_MAP3 = {
    "qwen": ["qwen" + prompt for prompt in PROMP_LIST3],
    "qwen-math": ["qwen-math" + prompt for prompt in PROMP_LIST3],
    "internlm": ["internlm"+prompt for prompt in PROMP_LIST3],
    "mistral": ["mistral"+prompt for prompt in PROMP_LIST3],
    "gemma": ["gemma"+prompt for prompt in PROMP_LIST3],
    "phi3mini": ["phi3mini"+prompt for prompt in PROMP_LIST3],
    "phi3small": ["phi3small"+prompt for prompt in PROMP_LIST3],
    "phi3medium": ["phi3medium"+prompt for prompt in PROMP_LIST3],
    "phi4": ["phi4"+prompt for prompt in PROMP_LIST3],
    "deepseek-r1-distill": ["deepseek-r1-distill"+prompt for prompt in PROMP_LIST3],
    "llama": ["llama"+prompt for prompt in PROMP_LIST3]
}

In [7]:
def gen_budget_list(budget, data_name, model):
    if budget == -1:
        return [-1]
    elif budget == 1:
        o1_like_models = [
            "Qwen/QwQ-32B-Preview", 
            "Skywork/Skywork-o1-Open-Llama-3.1-8B", 
            "PowerInfer/SmallThinker-3B-Preview",
            "NovaSky-AI/Sky-T1-32B-Preview", 
            "deepseek-ai/DeepSeek-R1-Distill-Qwen-1.5B",
            "deepseek-ai/DeepSeek-R1-Distill-Qwen-7B",
            "deepseek-ai/DeepSeek-R1-Distill-Qwen-14B",
            "deepseek-ai/DeepSeek-R1-Distill-Qwen-32B",
            "deepseek-ai/DeepSeek-R1-Distill-Llama-8B"
        ]
        if model in o1_like_models: # maybe should extend to longer sequence
            if data_name == "gsm8k":
                budget_list = []
                for i in range(25, 300, 25):
                    budget_list.append(i)
                for i in range(300, 600, 50):
                    budget_list.append(i)
                for i in range(600, 1201, 100):
                    budget_list.append(i)
            elif data_name in ["math", "math500"]:
                budget_list = []
                for i in range(25, 600, 100):
                    budget_list.append(i)
                for i in range(600, 2401, 200):
                    budget_list.append(i)
        else:    
            if data_name == "gsm8k":
                budget_list = []
                for i in range(25, 300, 25):
                    budget_list.append(i)
                for i in range(300, 601, 50):
                    budget_list.append(i)
            elif data_name in ["math", "math500"]:
                budget_list = []
                for i in range(25, 300, 75):
                    budget_list.append(i)
                for i in range(300, 600, 100):
                    budget_list.append(i)
                for i in range(600, 1201, 100):
                    budget_list.append(i)

        
        return budget_list

In [8]:
dataset = "gsm8k"   
something = "_-1_seed0_t0.0_s0_e-1"

In [9]:
model_acc_dicts = {}

for model in model_list:
    model_acc_dict = {}
    budget_list = gen_budget_list(1, dataset, model)
    model_prompt_list3 = MODEL_SERIES_PROMPT_TYPE_MAP3[MODEL_SERIES_MAP[model]]
    for prompt_type in model_prompt_list3:
        acc_list = []
        for budget in budget_list:
            file_name = "test_" + prompt_type + something + "_b" + str(int(budget)) + "_metrics.json"
            file_path = os.path.join(file_dir, model, prompt_type, dataset, file_name)
            with open(file_path, "r") as f:
                acc_list.append(json.load(f)["acc"])
        model_acc_dict[prompt_type] = acc_list
    model_acc_dicts[model] = model_acc_dict

model_acc_dicts

{'NovaSky-AI/Sky-T1-32B-Preview': {'qwen-sbs': [37.3,
   38.4,
   40.7,
   44.0,
   50.9,
   58.5,
   65.0,
   72.6,
   77.6,
   81.4,
   85.8,
   89.0,
   92.6,
   94.2,
   95.6,
   96.0,
   95.9,
   95.8,
   95.9,
   95.9,
   96.1,
   96.2,
   96.1,
   96.1],
  'qwen-c2f': [38.7,
   44.6,
   50.2,
   56.0,
   62.9,
   70.0,
   76.1,
   82.6,
   85.4,
   87.6,
   90.0,
   90.8,
   92.6,
   93.6,
   94.5,
   94.7,
   94.6,
   94.8,
   95.3,
   95.1,
   95.2,
   95.4,
   95.5,
   95.5],
  'qwen-aav': [39.3,
   46.6,
   59.2,
   69.5,
   77.9,
   83.7,
   88.5,
   91.1,
   92.6,
   93.8,
   94.6,
   94.5,
   94.9,
   95.0,
   95.1,
   94.8,
   95.1,
   95.1,
   94.9,
   94.8,
   95.0,
   95.0,
   95.0,
   95.1]},
 'Qwen/QwQ-32B-Preview': {'qwen-sbs': [35.4,
   36.2,
   36.5,
   37.5,
   41.5,
   45.7,
   51.0,
   60.0,
   65.8,
   71.0,
   75.7,
   80.1,
   84.8,
   89.0,
   91.0,
   93.7,
   94.5,
   94.6,
   94.8,
   95.5,
   95.3,
   95.5,
   95.5,
   95.2],
  'qwen-c2f': [36.4,
   41

In [10]:
# import seaborn as sns

# # Set Seaborn style
# sns.set_style(style="whitegrid", rc={"grid.linewidth": 8, "grid.color": "0.7"})
# fig, axs = plt.subplots(12,7, figsize=(100, 160))
# line_width = 8   # Set the desiorange line width
# line_shape = {
#     "hard": "--",
#     "budget": "-.",
#     "else": "-"
# }
# color = {
#     "sbs": "orange",
#     "c2f": "green",
#     "aav": "#B771E5"
# }
# # set the title
# fig.suptitle(f"{dataset}".upper(), fontsize=170, y=0.93)

# # Flatten the axes array for easy iteration
# axs = axs.flatten()

# # Plot all lines first without labels
# for index, model in enumerate(model_list):
#     budget_list = gen_budget_list(1, dataset, model)
#     model_prompt_list = MODEL_SERIES_PROMPT_TYPE_MAP1[MODEL_SERIES_MAP[model]]
    
#     for prompt_type in model_prompt_list:
#         if "sbs-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7))].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="orange", label="sbs-hard", linewidth=line_width)
#         elif "c2f-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7))].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="green", label="c2f-hard", linewidth=line_width)
#         elif "aav-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7))].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="#B771E5", label="aav-hard", linewidth=line_width)
#         elif "sbs" in prompt_type:
#             axs[int((index//7) * 21 + (index%7))].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="orange", label="sbs", linewidth=line_width)
#         elif "c2f" in prompt_type:
#             axs[int((index//7) * 21 + (index%7))].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="green", label="c2f", linewidth=line_width)
#         elif "aav" in prompt_type:
#             axs[int((index//7) * 21 + (index%7))].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="#B771E5", label="aav", linewidth=line_width)
        
#         axs[int((index//7) * 21 + (index%7))].set_xlabel("Token Budget", fontsize=50)
#         axs[int((index//7) * 21 + (index%7))].set_ylabel("Accuracy", fontsize=50)
#         axs[int((index//7) * 21 + (index%7))].set_title(f"{model.split('/')[-1]}", fontsize=50, y=1.05)
#         axs[int((index//7) * 21 + (index%7))].tick_params(axis='both', which='major', labelsize=50)
#         # axs[index].set_xticks(range(0, 551, 50))  # Set x-axis interval to 50
#     model_prompt_list = MODEL_SERIES_PROMPT_TYPE_MAP2[MODEL_SERIES_MAP[model]]
#     for prompt_type in model_prompt_list:
#         if "sbs-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 7)].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="orange", label="sbs-hard", linewidth=line_width)
#         elif "c2f-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 7)].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="green", label="c2f-hard", linewidth=line_width)
#         elif "aav-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 7)].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="#B771E5", label="aav-hard", linewidth=line_width)
#         elif "sbs" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 7)].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="orange", label="sbs", linewidth=line_width)
#         elif "c2f" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 7)].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="green", label="c2f", linewidth=line_width)
#         elif "aav" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 7)].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="#B771E5", label="aav", linewidth=line_width)
        
#         axs[int((index//7) * 21 + (index%7) + 7)].set_xlabel("Token Budget", fontsize=50)
#         axs[int((index//7) * 21 + (index%7) + 7)].set_ylabel("Accuracy", fontsize=50)
#         axs[int((index//7) * 21 + (index%7) + 7)].set_title(f"{model.split('/')[-1]}", fontsize=50, y=1.05)  
#         axs[int((index//7) * 21 + (index%7) + 7)].tick_params(axis='both', which='major', labelsize=50) 
#     model_prompt_list = MODEL_SERIES_PROMPT_TYPE_MAP3[MODEL_SERIES_MAP[model]]
#     for prompt_type in model_prompt_list:
#         if "sbs-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 14)].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="orange", label="sbs-hard", linewidth=line_width)
#         elif "c2f-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 14)].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="green", label="c2f-hard", linewidth=line_width)
#         elif "aav-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 14)].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="#B771E5", label="aav-hard", linewidth=line_width)
#         elif "sbs" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 14)].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="orange", label="sbs", linewidth=line_width)
#         elif "c2f" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 14)].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="green", label="c2f", linewidth=line_width)
#         elif "aav" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 14)].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="#B771E5", label="aav", linewidth=line_width)
        
#         axs[int((index//7) * 21 + (index%7) + 14)].set_xlabel("Token Budget", fontsize=50)
#         axs[int((index//7) * 21 + (index%7) + 14)].set_ylabel("Accuracy", fontsize=50)
#         axs[int((index//7) * 21 + (index%7) + 14)].set_title(f"{model.split('/')[-1]}", fontsize=50, y=1.05) 
#         axs[int((index//7) * 21 + (index%7) + 14)].tick_params(axis='both', which='major', labelsize=50) 

# for ax in axs:
#     for spine in ax.spines.values():
#         spine.set_linewidth(2)
#         spine.set_color('black')
# # Adjust layout
# plt.tight_layout()
# # fig.subplots_adjust(top=0.9)
# plt.subplots_adjust(
#     left=0.1,      # Left margin
#     right=0.9,     # Right margin
#     bottom=0.1,    # Bottom margin
#     top=0.9,       # Top margin
#     wspace=0.6,    # Width spacing between subplots
#     hspace=0.4     # Height spacing between subplots
# )
# plt.savefig("gsm8k_all.pdf")   

In [11]:
import seaborn as sns

# Set Seaborn style
sns.set_style(style="whitegrid", rc={"grid.linewidth": 8, "grid.color": "0.7"})
fig, axs = plt.subplots(5,6, figsize=(100, 70))
line_width = 12   # Set the desiorange line width
line_shape = {
    "hard": "--",
    "budget": "-.",
    "else": "-"
}
color = {
    "sbs": "orange",
    "c2f": "green",
    "aav": "#B771E5"
}
# set the title
fig.suptitle(f"{dataset}".upper(), fontsize=140, y=0.93)

# Flatten the axes array for easy iteration
axs = axs.flatten()

# Plot all lines first without labels
for index, model in enumerate(model_list):
    budget_list = gen_budget_list(1, dataset, model)
    model_prompt_list = MODEL_SERIES_PROMPT_TYPE_MAP3[MODEL_SERIES_MAP[model]]
    
    for prompt_type in model_prompt_list:
        if "sbs-hard" in prompt_type:
            axs[index].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="orange", label="sbs-hard", linewidth=line_width)
        elif "c2f-hard" in prompt_type:
            axs[index].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="green", label="c2f-hard", linewidth=line_width)
        elif "aav-hard" in prompt_type:
            axs[index].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="#B771E5", label="aav-hard", linewidth=line_width)
        elif "sbs" in prompt_type:
            axs[index].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="orange", label="sbs", linewidth=line_width)
        elif "c2f" in prompt_type:
            axs[index].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="green", label="c2f", linewidth=line_width)
        elif "aav" in prompt_type:
            axs[index].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="#B771E5", label="aav", linewidth=line_width)
        
        axs[int(index)].set_xlabel("Token Budget", fontsize=70)
        axs[int(index)].set_ylabel("Accuracy", fontsize=70)
        axs[int(0)].set_title("Sky-T1-32B", fontsize=80, y=1.05)
        axs[int(1)].set_title("QwQ-32B", fontsize=80, y=1.05)
        axs[int(2)].set_title("Qwen-2.5-72B", fontsize=80, y=1.05)
        axs[int(3)].set_title("Qwen-2.5-32B", fontsize=80, y=1.05)
        axs[int(4)].set_title("Qwen-2.5-14B", fontsize=80, y=1.05)
        axs[int(5)].set_title("Qwen-2.5-7B", fontsize=80, y=1.05)
        axs[int(6)].set_title("Qwen-2.5-3B", fontsize=80, y=1.05)
        axs[int(7)].set_title("Qwen-2.5-1.5B", fontsize=80, y=1.05)
        axs[int(8)].set_title("Qwen-2.5-Math-1.5B", fontsize=80, y=1.05)
        axs[int(9)].set_title("Qwen-2.5-Math-7B", fontsize=80, y=1.05)
        axs[int(10)].set_title("Mistral-Small", fontsize=80, y=1.05)
        axs[int(11)].set_title("Mistral-Nemo", fontsize=80, y=1.05)
        axs[int(12)].set_title("Ministral-8B", fontsize=80, y=1.05)
        axs[int(13)].set_title("Mathstral-7B", fontsize=80, y=1.05)
        axs[int(14)].set_title("gemma-2-27B", fontsize=80, y=1.05)
        axs[int(15)].set_title("gemma-2-9B", fontsize=80, y=1.05)
        axs[int(16)].set_title("gemma-2-2B", fontsize=80, y=1.05)
        axs[int(17)].set_title("Phi-3-medium", fontsize=80, y=1.05)
        axs[int(18)].set_title("Phi-3-small", fontsize=80, y=1.05)
        axs[int(19)].set_title("Phi-3-mini", fontsize=80, y=1.05)
        axs[int(20)].set_title("Phi-3.5-mini", fontsize=80, y=1.05)
        axs[int(21)].set_title("Phi-4", fontsize=80, y=1.05)
        axs[int(22)].set_title("DRD-Qwen-1.5B", fontsize=80, y=1.05)
        axs[int(23)].set_title("DRD-Qwen-7B", fontsize=80, y=1.05)
        axs[int(24)].set_title("DRD-Qwen-14B", fontsize=80, y=1.05)
        axs[int(25)].set_title("DRD-Qwen-32B", fontsize=80, y=1.05)
        axs[int(26)].set_title("Llama-3.2-3B", fontsize=80, y=1.05)
        axs[int(27)].set_title("Llama-3.2-1B", fontsize=80, y=1.05)
        axs[int(28)].set_title("Llama-3.1-8B", fontsize=80, y=1.05)
        axs[int(29)].set_title("Llama-3.1-70B", fontsize=80, y=1.05)
        axs[int(index)].tick_params(axis='both', which='major', labelsize=60)

for ax in axs:
    for spine in ax.spines.values():
        spine.set_linewidth(2)
        spine.set_color('black')

from matplotlib.lines import Line2D
legend_lines = [
    Line2D([0], [0], color='orange', linestyle='-', linewidth=line_width, label='sbs'),
    Line2D([0], [0], color='green', linestyle='-', linewidth=line_width, label='c2f'),
    Line2D([0], [0], color='#B771E5', linestyle='-', linewidth=line_width, label='aav')
]

# Add single legend to figure
fig.legend(handles=legend_lines,
        loc='upper center',
        bbox_to_anchor=(0.5, 0.88),
        ncol=6,
        columnspacing=12.0,      # Adjust spacing between columns (default is 2.0)
        handletextpad=0.4,      # Adjust spacing between line and text (default is 0.8)
        borderpad=0.4,          # Adjust internal padding (default is 0.4)
        fontsize=100,
        frameon=False,
        fancybox=False,
        shadow=True)
# Adjust layout
plt.tight_layout()
# fig.subplots_adjust(top=0.9)
plt.subplots_adjust(
    left=0.04,      # Left margin
    right=0.98,     # Right margin
    bottom=0.04,    # Bottom margin
    top=0.8,       # Top margin
    wspace=0.3,    # Width spacing between subplots
    hspace=0.5     # Height spacing between subplots
)
plt.savefig("gsm8k_all.pdf")   

In [12]:
dataset = "math500"   
something = "_-1_seed0_t0.0_s0_e-1"

In [13]:
model_acc_dicts = {}

for model in model_list:
    model_acc_dict = {}
    budget_list = gen_budget_list(1, dataset, model)
    model_prompt_list3 = MODEL_SERIES_PROMPT_TYPE_MAP3[MODEL_SERIES_MAP[model]]
    for prompt_type in model_prompt_list3:
        acc_list = []
        for budget in budget_list:
            file_name = "test_" + prompt_type + something + "_b" + str(int(budget)) + "_metrics.json"
            file_path = os.path.join(file_dir, model, prompt_type, dataset, file_name)
            with open(file_path, "r") as f:
                acc_list.append(json.load(f)["acc"])
        model_acc_dict[prompt_type] = acc_list
    model_acc_dicts[model] = model_acc_dict

model_acc_dicts

{'NovaSky-AI/Sky-T1-32B-Preview': {'qwen-sbs': [34.6,
   36.6,
   45.0,
   55.2,
   61.6,
   66.4,
   70.6,
   76.6,
   80.6,
   84.0,
   84.8,
   86.0,
   87.6,
   88.2,
   88.0,
   88.0],
  'qwen-c2f': [37.4,
   43.2,
   50.4,
   58.0,
   64.2,
   68.0,
   70.4,
   76.0,
   79.8,
   81.2,
   81.6,
   82.8,
   83.2,
   83.2,
   84.0,
   84.8],
  'qwen-aav': [36.8,
   44.6,
   55.2,
   62.8,
   69.0,
   71.8,
   73.6,
   76.6,
   80.4,
   82.2,
   82.8,
   84.2,
   84.2,
   84.4,
   84.6,
   84.8]},
 'Qwen/QwQ-32B-Preview': {'qwen-sbs': [33.0,
   34.6,
   37.6,
   46.6,
   53.0,
   56.6,
   62.4,
   69.2,
   74.0,
   79.4,
   81.2,
   81.8,
   82.2,
   83.2,
   84.6,
   84.0],
  'qwen-c2f': [34.8,
   38.8,
   45.0,
   52.0,
   57.4,
   63.8,
   68.2,
   72.4,
   76.6,
   80.4,
   82.0,
   82.4,
   84.0,
   84.4,
   84.6,
   86.0],
  'qwen-aav': [35.0,
   37.2,
   43.6,
   52.2,
   58.4,
   64.0,
   68.8,
   75.0,
   78.2,
   80.8,
   81.8,
   82.2,
   83.0,
   83.8,
   85.0,
   85.6]},

In [14]:
# import seaborn as sns

# # Set Seaborn style
# sns.set_style(style="whitegrid", rc={"grid.linewidth": 8, "grid.color": "0.7"})
# fig, axs = plt.subplots(12,7, figsize=(100, 160))
# line_width = 8   # Set the desiorange line width
# line_shape = {
#     "hard": "--",
#     "budget": "-.",
#     "else": "-"
# }
# color = {
#     "sbs": "orange",
#     "c2f": "green",
#     "aav": "#B771E5"
# }
# # set the title
# fig.suptitle(f"{dataset}".upper(), fontsize=170, y=0.93)

# # Flatten the axes array for easy iteration
# axs = axs.flatten()

# # Plot all lines first without labels
# for index, model in enumerate(model_list):
#     budget_list = gen_budget_list(1, dataset, model)
#     model_prompt_list = MODEL_SERIES_PROMPT_TYPE_MAP1[MODEL_SERIES_MAP[model]]
    
#     for prompt_type in model_prompt_list:
#         if "sbs-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7))].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="orange", label="sbs-hard", linewidth=line_width)
#         elif "c2f-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7))].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="green", label="c2f-hard", linewidth=line_width)
#         elif "aav-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7))].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="#B771E5", label="aav-hard", linewidth=line_width)
#         elif "sbs" in prompt_type:
#             axs[int((index//7) * 21 + (index%7))].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="orange", label="sbs", linewidth=line_width)
#         elif "c2f" in prompt_type:
#             axs[int((index//7) * 21 + (index%7))].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="green", label="c2f", linewidth=line_width)
#         elif "aav" in prompt_type:
#             axs[int((index//7) * 21 + (index%7))].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="#B771E5", label="aav", linewidth=line_width)
        
#         axs[int((index//7) * 21 + (index%7))].set_xlabel("Token Budget", fontsize=50)
#         axs[int((index//7) * 21 + (index%7))].set_ylabel("Accuracy", fontsize=50)
#         axs[int((index//7) * 21 + (index%7))].set_title(f"{model.split('/')[-1]}", fontsize=50, y=1.05)
#         axs[int((index//7) * 21 + (index%7))].tick_params(axis='both', which='major', labelsize=50)
#         # axs[index].set_xticks(range(0, 551, 50))  # Set x-axis interval to 50
#     model_prompt_list = MODEL_SERIES_PROMPT_TYPE_MAP2[MODEL_SERIES_MAP[model]]
#     for prompt_type in model_prompt_list:
#         if "sbs-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 7)].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="orange", label="sbs-hard", linewidth=line_width)
#         elif "c2f-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 7)].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="green", label="c2f-hard", linewidth=line_width)
#         elif "aav-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 7)].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="#B771E5", label="aav-hard", linewidth=line_width)
#         elif "sbs" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 7)].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="orange", label="sbs", linewidth=line_width)
#         elif "c2f" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 7)].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="green", label="c2f", linewidth=line_width)
#         elif "aav" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 7)].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="#B771E5", label="aav", linewidth=line_width)
        
#         axs[int((index//7) * 21 + (index%7) + 7)].set_xlabel("Token Budget", fontsize=50)
#         axs[int((index//7) * 21 + (index%7) + 7)].set_ylabel("Accuracy", fontsize=50)
#         axs[int((index//7) * 21 + (index%7) + 7)].set_title(f"{model.split('/')[-1]}", fontsize=50, y=1.05)  
#         axs[int((index//7) * 21 + (index%7) + 7)].tick_params(axis='both', which='major', labelsize=50) 
#     model_prompt_list = MODEL_SERIES_PROMPT_TYPE_MAP3[MODEL_SERIES_MAP[model]]
#     for prompt_type in model_prompt_list:
#         if "sbs-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 14)].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="orange", label="sbs-hard", linewidth=line_width)
#         elif "c2f-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 14)].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="green", label="c2f-hard", linewidth=line_width)
#         elif "aav-hard" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 14)].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="#B771E5", label="aav-hard", linewidth=line_width)
#         elif "sbs" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 14)].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="orange", label="sbs", linewidth=line_width)
#         elif "c2f" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 14)].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="green", label="c2f", linewidth=line_width)
#         elif "aav" in prompt_type:
#             axs[int((index//7) * 21 + (index%7) + 14)].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="#B771E5", label="aav", linewidth=line_width)
        
#         axs[int((index//7) * 21 + (index%7) + 14)].set_xlabel("Token Budget", fontsize=50)
#         axs[int((index//7) * 21 + (index%7) + 14)].set_ylabel("Accuracy", fontsize=50)
#         axs[int((index//7) * 21 + (index%7) + 14)].set_title(f"{model.split('/')[-1]}", fontsize=50, y=1.05) 
#         axs[int((index//7) * 21 + (index%7) + 14)].tick_params(axis='both', which='major', labelsize=50) 

# for ax in axs:
#     for spine in ax.spines.values():
#         spine.set_linewidth(2)
#         spine.set_color('black')
# # Adjust layout
# plt.tight_layout()
# # fig.subplots_adjust(top=0.9)
# plt.subplots_adjust(
#     left=0.1,      # Left margin
#     right=0.9,     # Right margin
#     bottom=0.1,    # Bottom margin
#     top=0.9,       # Top margin
#     wspace=0.6,    # Width spacing between subplots
#     hspace=0.4     # Height spacing between subplots
# )
# plt.savefig("math500_all.pdf")   

In [15]:
import seaborn as sns

# Set Seaborn style
sns.set_style(style="whitegrid", rc={"grid.linewidth": 8, "grid.color": "0.7"})
fig, axs = plt.subplots(5,6, figsize=(100, 70))
line_width = 12   # Set the desiorange line width
line_shape = {
    "hard": "--",
    "budget": "-.",
    "else": "-"
}
color = {
    "sbs": "orange",
    "c2f": "green",
    "aav": "#B771E5"
}
# set the title
fig.suptitle(f"{dataset}".upper(), fontsize=140, y=0.93)

# Flatten the axes array for easy iteration
axs = axs.flatten()

# Plot all lines first without labels
for index, model in enumerate(model_list):
    budget_list = gen_budget_list(1, dataset, model)
    model_prompt_list = MODEL_SERIES_PROMPT_TYPE_MAP3[MODEL_SERIES_MAP[model]]
    
    for prompt_type in model_prompt_list:
        if "sbs-hard" in prompt_type:
            axs[index].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="orange", label="sbs-hard", linewidth=line_width)
        elif "c2f-hard" in prompt_type:
            axs[index].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="green", label="c2f-hard", linewidth=line_width)
        elif "aav-hard" in prompt_type:
            axs[index].plot(budget_list, model_acc_dicts[model][prompt_type], linestyle='--', color="#B771E5", label="aav-hard", linewidth=line_width)
        elif "sbs" in prompt_type:
            axs[index].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="orange", label="sbs", linewidth=line_width)
        elif "c2f" in prompt_type:
            axs[index].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="green", label="c2f", linewidth=line_width)
        elif "aav" in prompt_type:
            axs[index].plot([budget + 25 for budget in budget_list], model_acc_dicts[model][prompt_type], linestyle='-', color="#B771E5", label="aav", linewidth=line_width)
        
        axs[int(index)].set_xlabel("Token Budget", fontsize=70)
        axs[int(index)].set_ylabel("Accuracy", fontsize=70)
        axs[int(0)].set_title("Sky-T1-32B", fontsize=80, y=1.05)
        axs[int(1)].set_title("QwQ-32B", fontsize=80, y=1.05)
        axs[int(2)].set_title("Qwen-2.5-72B", fontsize=80, y=1.05)
        axs[int(3)].set_title("Qwen-2.5-32B", fontsize=80, y=1.05)
        axs[int(4)].set_title("Qwen-2.5-14B", fontsize=80, y=1.05)
        axs[int(5)].set_title("Qwen-2.5-7B", fontsize=80, y=1.05)
        axs[int(6)].set_title("Qwen-2.5-3B", fontsize=80, y=1.05)
        axs[int(7)].set_title("Qwen-2.5-1.5B", fontsize=80, y=1.05)
        axs[int(8)].set_title("Qwen-2.5-Math-1.5B", fontsize=80, y=1.05)
        axs[int(9)].set_title("Qwen-2.5-Math-7B", fontsize=80, y=1.05)
        axs[int(10)].set_title("Mistral-Small", fontsize=80, y=1.05)
        axs[int(11)].set_title("Mistral-Nemo", fontsize=80, y=1.05)
        axs[int(12)].set_title("Ministral-8B", fontsize=80, y=1.05)
        axs[int(13)].set_title("Mathstral-7B", fontsize=80, y=1.05)
        axs[int(14)].set_title("gemma-2-27B", fontsize=80, y=1.05)
        axs[int(15)].set_title("gemma-2-9B", fontsize=80, y=1.05)
        axs[int(16)].set_title("gemma-2-2B", fontsize=80, y=1.05)
        axs[int(17)].set_title("Phi-3-medium", fontsize=80, y=1.05)
        axs[int(18)].set_title("Phi-3-small", fontsize=80, y=1.05)
        axs[int(19)].set_title("Phi-3-mini", fontsize=80, y=1.05)
        axs[int(20)].set_title("Phi-3.5-mini", fontsize=80, y=1.05)
        axs[int(21)].set_title("Phi-4", fontsize=80, y=1.05)
        axs[int(22)].set_title("DRD-Qwen-1.5B", fontsize=80, y=1.05)
        axs[int(23)].set_title("DRD-Qwen-7B", fontsize=80, y=1.05)
        axs[int(24)].set_title("DRD-Qwen-14B", fontsize=80, y=1.05)
        axs[int(25)].set_title("DRD-Qwen-32B", fontsize=80, y=1.05)
        axs[int(26)].set_title("Llama-3.2-3B", fontsize=80, y=1.05)
        axs[int(27)].set_title("Llama-3.2-1B", fontsize=80, y=1.05)
        axs[int(28)].set_title("Llama-3.1-8B", fontsize=80, y=1.05)
        axs[int(29)].set_title("Llama-3.1-70B", fontsize=80, y=1.05)
        axs[int(index)].tick_params(axis='both', which='major', labelsize=60)
for ax in axs:
    for spine in ax.spines.values():
        spine.set_linewidth(2)
        spine.set_color('black')

from matplotlib.lines import Line2D
legend_lines = [
    Line2D([0], [0], color='orange', linestyle='-', linewidth=line_width, label='sbs'),
    Line2D([0], [0], color='green', linestyle='-', linewidth=line_width, label='c2f'),
    Line2D([0], [0], color='#B771E5', linestyle='-', linewidth=line_width, label='aav')
]

# Add single legend to figure
fig.legend(handles=legend_lines,
        loc='upper center',
        bbox_to_anchor=(0.5, 0.88),
        ncol=6,
        columnspacing=12.0,      # Adjust spacing between columns (default is 2.0)
        handletextpad=0.4,      # Adjust spacing between line and text (default is 0.8)
        borderpad=0.4,          # Adjust internal padding (default is 0.4)
        fontsize=100,
        frameon=False,
        fancybox=False,
        shadow=True)
# Adjust layout
plt.tight_layout()
# fig.subplots_adjust(top=0.9)
plt.subplots_adjust(
    left=0.04,      # Left margin
    right=0.98,     # Right margin
    bottom=0.04,    # Bottom margin
    top=0.8,       # Top margin
    wspace=0.3,    # Width spacing between subplots
    hspace=0.5     # Height spacing between subplots
)
plt.savefig("math500_all.pdf")   